# Yu et al - "Math modeling of fluconazole resistance in C. albicans"

## Study 1: Calibration of model without azole (Table S1)

In [ ]:
# Imports
import numpy as np
from scipy.integrate import odeint
import matplotlib.pyplot as plt
import matplotlib as mpl

mpl.rcParams['lines.linewidth'] = 6
mpl.rc('axes', labelsize = 24)
mpl.rcParams.update({'font.size': 14})
mpl.rcParams['legend.loc'] = 'best'

# Model without azole
def model(y, t, k):
  # Initial condition
  R1 = y[0]
  E1tot = y[1]
  C1 = y[2]
  R2 = y[3]
  E2tot = y[4]
  C2 = y[5]
  R3 = y[6]
  E3tot = y[7]
  C3 = y[8]
  P = y[9]
  R1a = y[10]
  C1a = y[11]
  C2a = y[12]
  R2a = y[13]
  R3a = y[14]
  R4a = y[15]
  C3a = y[16]
  Pa = y[17]

  # Parameters (Kelly, 1997)
  ## Lanosterol-C14a-demethylase Complex
  kf1 = k[0]
  kb1 = k[1]
  kf4 = k[2]

  ## Zymosterol-Sterol-methyltransferase Complex
  kf2 = k[3]
  kb2 = k[4]
  kf5 = k[5]

  ## Episterol-C5-desaturase Complex
  kf3 = k[6]
  kb3 = k[7]
  kf6 = k[8]

  ## Alternative pathway
  kf1a = k[9]
  kb1a = k[10]
  kf2a = k[11]
  kb2a = k[12]
  kf4a = k[13]
  kf3a = k[14]
  kb3a = k[15]
  kf7a = k[16]
  kf5a = k[17]
  kf6a = k[18]

  # Constraint
  E1 = E1tot - C1 - C1a
  E2 = E2tot - C2 - C2a
  E3 = E3tot - C3 - C3a
  
  # ODEs
  dR1dt = kb1*C1 + kb2a*C2a - kf1*R1*E1 - kf2a*R1*E2
  dE1dt = kb1*C1 + kf4*C1 + kb1a*C1a - kf1*R1*E1 - kf1a*R1a*E1
  dC1dt = kf1*R1*E1 - kb1*C1 - kf4*C1
  dR2dt = kf4*C1 + kb2*C2 - kf2*R2*E2
  dE2dt = kb2*C2 + kf5*C2 + kb2a*C2a + kf4a*C2a- kf2*R2*E2 - kf2a*R1*E2
  dC2dt = kf2*R2*E2 - kb2*C2 - kf5*C2
  dR3dt = kf5*C2 + kb3*C3 - kf3*R3*E3
  dE3dt = kb3*C3 + kf6*C3 + kb3a*C3a + kf7a*C3a - kf3*R3*E3 - kf3a*R4a*E3
  dC3dt = kf3*R3*E3 - kb3*C3 - kf6*C3
  dPdt = kf6*C3

  dR1adt = kb1a*C1a - kf1a*R1a*E1
  dC1adt = kf1a*R1a*E1 - kb1a*C1a
  dC2adt = kf2a*R1*E2 - kb2a*C2a - kf4a*C2a
  dR2adt = kf4a*C2a - kf5a*R2a
  dR3adt = kf5a*R2a - kf6a*R3a
  dR4adt = kf6a*R3a + kb3a*C3a - kf3a*R4a*E3
  dC3adt = kf3a*R4a*E3 - kb3a*C3a - kf7a*C3a
  dPadt = kf7a*C3a 

  dydt = [dR1dt, dE1dt, dC1dt, dR2dt, dE2dt, dC2dt, dR3dt, dE3dt, dC3dt, dPdt, dR1adt, dC1adt, dC2adt, dR2adt, dR3adt, dR4adt, dC3adt, dPadt]
  return dydt

# R1 - Lanosterol
# E1 - C14a-demethylase
# C1 - Lanosterol-C14a-demethylase Complex
# R2 - Zymosterol
# E2 - Sterol-methyltransferase
# C2 - Zymosterol-Sterol-methyltransferase Complex
# R3 - Episterol
# E3 - C5-desaturase
# C3 - Episterol-C5-desaturase Complex
# P - Ergosterol
# R1a - Azole
# C1a - Azole-C14a-demethylase Complex
# C2a - Lanosterol-Sterol-methyltransferase Complex
# R2a - Eburicol
# R3a - Obtusifoliol
# R4a - 14a-methylfecosterol
# C3a - 14a-methylfecosterol-C5-desaturase Complex
# Pa - 14a-methyl-3,6-diol

STEPS = 10000
DAYS = 1

AZOLE_FIT = 52.24*DAYS      # 16 ug/ml (Kelly, 1997)
LANOSTEROL = 25*AZOLE_FIT
ENZYME = 2*AZOLE_FIT

# Initial condition 
## States [R1,E1,C1,R2,E2,C2,R3,E3,C3,P,R1a,C1a,C2a,R2a,R3a,R4a,C3a,Pa]
Y0_s1 = [LANOSTEROL,ENZYME,0,0,ENZYME,0,0,ENZYME,0,0,0,0,0,0,0,0,0,0]

## Parameters [kf1,kb1,kf4,kf2,kb2,kf5,kf3,kb3,kf6,kf1a,kb1a,kf2a,kb2a,kf4a,kf3a,kb3a,kf7a,kf5a,kf6a]
K0_no_azole = [0.0000825,0.1,0.1,0.00017,0.1,0.1,0.1,0.1,0.017378,0,0,0,0,0,0,0,0,0,0]

y_s1 = []

# Time span (in minutes)
t = np.linspace(0, DAYS*24*60, DAYS*STEPS)

y_s1 = odeint(model, Y0_s1, t, (K0_no_azole,))

# Sterol Composition (Kelly, 1997)
# R1 - Lanosterol: 0.66%
# R2 - Zymosterol: 0.66%
# R3 - Episterol: 0.66%
# P - Ergosterol: 98%
# R2a - Eburicol: 0%
# R3a - Obtusifoliol: 0%
# R4a - 14a-methylfecosterol: 0%
# Pa - 14a-methyl-3,6-diol: 0%
sterol_total = y_s1[-1,0] + y_s1[-1,3] + y_s1[-1,6] + y_s1[-1,9] + y_s1[-1,13] + y_s1[-1,14] + y_s1[-1,15] + y_s1[-1,17]
print('Lanosterol: {val:.2f} ({pct:.2f}%)'.format(val=y_s1[-1,0], pct=(y_s1[-1,0]/sterol_total)*100))
print('Zymosterol: {val:.2f} ({pct:.2f}%)'.format(val=y_s1[-1,3], pct=(y_s1[-1,3]/sterol_total)*100))
print('Episterol: {val:.2f} ({pct:.2f}%)'.format(val=y_s1[-1,6], pct=(y_s1[-1,6]/sterol_total)*100))
print('Ergosterol: {val:.2f} ({pct:.2f}%)'.format(val=y_s1[-1,9], pct=(y_s1[-1,9]/sterol_total)*100))
print('')
print('Eburicol: {val:.2f} ({pct:.2f}%)'.format(val=y_s1[-1,13], pct=(y_s1[-1,13]/sterol_total)*100))
print('Obtusifoliol: {val:.2f} ({pct:.2f}%)'.format(val=y_s1[-1,14], pct=(y_s1[-1,14]/sterol_total)*100))
print('14a-methylfecosterol: {val:.2f} ({pct:.2f}%)'.format(val=y_s1[-1,15], pct=(y_s1[-1,15]/sterol_total)*100))
print('14a-methyl-3,6-diol: {val:.2f} ({pct:.2f}%)'.format(val=y_s1[-1,17], pct=(y_s1[-1,17]/sterol_total)*100))
print('')
print('% Ergosterol reduction: {pct:.2f}%'.format(pct=((y_s1[-1,9]-y_s1[-1,9])/y_s1[-1,9])*100))

Lanosterol: 8.26 (0.66%)
Zymosterol: 8.46 (0.67%)
Episterol: 8.37 (0.67%)
Ergosterol: 1230.86 (98.00%)

Eburicol: 0.00 (0.00%)
Obtusifoliol: 0.00 (0.00%)
14a-methylfecosterol: 0.00 (0.00%)
14a-methyl-3,6-diol: 0.00 (0.00%)

% Ergosterol reduction: 0.00%


### Plot model without azole

In [ ]:
# Plot
fig, axs = plt.subplots(5, 4, sharex=True, sharey=False, figsize=(38,38), dpi=300)
BLACK = 'k'

axs[0,0].plot(t/60, y_s1[:,0], color=BLACK, label='(-) Azole')
axs[0,0].set_ylabel('Lanosterol [uM]')
axs[0,0].legend()

axs[0,1].plot(t/60, y_s1[:,1], color=BLACK)
axs[0,1].set_ylabel('C14a-demethylase [uM]')

axs[0,2].plot(t/60, y_s1[:,2], color=BLACK)
axs[0,2].set_ylabel('Lanosterol-\nC14a-demethylase [uM]')

axs[0,3].plot(t/60, y_s1[:,3], color=BLACK)
axs[0,3].set_ylabel('Zymosterol [uM]')

axs[1,0].plot(t/60, y_s1[:,4], color=BLACK)
axs[1,0].set_ylabel('Sterol-methyltransferase [uM]')

axs[1,1].plot(t/60, y_s1[:,5], color=BLACK)
axs[1,1].set_ylabel('Zymosterol-\nSterol-methyltransferase [uM]')

axs[1,2].plot(t/60, y_s1[:,6], color=BLACK)
axs[1,2].set_ylabel('Episterol [uM]')

axs[1,3].plot(t/60, y_s1[:,7], color=BLACK)
axs[1,3].set_ylabel('C5-desaturase [uM]')

axs[2,0].plot(t/60, y_s1[:,8], color=BLACK)
axs[2,0].set_ylabel('Episterol-C5-desaturase [uM]')

axs[2,1].plot(t/60, y_s1[:,9], color=BLACK)
axs[2,1].set_ylabel('Ergosterol [uM]')

axs[2,2].plot(t/60, y_s1[:,10], color=BLACK)
axs[2,2].set_ylabel('Azole [uM]')

axs[2,3].plot(t/60, y_s1[:,11], color=BLACK)
axs[2,3].set_ylabel('Azole-C14a-demethylase [uM]')

axs[3,0].plot(t/60, y_s1[:,12], color=BLACK)
axs[3,0].set_ylabel('Lanosterol-\nSterol-methyltransferase [uM]')

axs[3,1].plot(t/60, y_s1[:,13], color=BLACK)
axs[3,1].set_ylabel('Eburicol [uM]')

axs[3,2].plot(t/60, y_s1[:,14], color=BLACK)
axs[3,2].set_ylabel('Obtusifoliol [uM]')

axs[3,3].plot(t/60, y_s1[:,15], color=BLACK)
axs[3,3].set_ylabel('14a-methylfecosterol [uM]')

axs[4,0].plot(t/60, y_s1[:,16], color=BLACK)
axs[4,0].set_xlabel('Time [h]')
axs[4,0].set_ylabel('14a-methylfecosterol-\nC5-desaturase [uM]')

axs[4,1].plot(t/60, y_s1[:,17], color=BLACK)
axs[4,1].set_xlabel('Time [h]')
axs[4,1].set_ylabel('14a-methyl-3,6-diol [uM]')

axs[4,2].plot(t/60, y_s1[:,9], color=BLACK)
axs[4,2].set_xlabel('Time [h]')
axs[4,2].set_ylabel('Ergosterol [uM]')
axs[4,2].spines['bottom'].set_lw(4)
axs[4,2].spines['top'].set_lw(4)
axs[4,2].spines['right'].set_lw(4)
axs[4,2].spines['left'].set_lw(4)

axs[4,3].plot(t/60, y_s1[:,17], color=BLACK)
axs[4,3].set_xlabel('Time [h]')
axs[4,3].set_ylabel('Toxic sterol [uM]')
axs[4,3].spines['bottom'].set_lw(4)
axs[4,3].spines['top'].set_lw(4)
axs[4,3].spines['right'].set_lw(4)
axs[4,3].spines['left'].set_lw(4)

fig.show()


## Study 2: Model calibration to Kelly et al. (1997) (Table S1)

In [ ]:
# R1 - Lanosterol
# E1 - C14a-demethylase
# C1 - Lanosterol-C14a-demethylase Complex
# R2 - Zymosterol
# E2 - Sterol-methyltransferase
# C2 - Zymosterol-Sterol-methyltransferase Complex
# R3 - Episterol
# E3 - C5-desaturase
# C3 - Episterol-C5-desaturase Complex
# P - Ergosterol
# R1a - Azole
# C1a - Azole-C14a-demethylase Complex
# C2a - Lanosterol-Sterol-methyltransferase Complex
# R2a - Eburicol
# R3a - Obtusifoliol
# R4a - 14a-methylfecosterol
# C3a - 14a-methylfecosterol-C5-desaturase Complex
# Pa - 14a-methyl-3,6-diol

STEPS = 10000
DAYS = 1

AZOLE_FIT = 52.24*DAYS      # 16 ug/ml (Kelly, 1997)
LANOSTEROL = 25*AZOLE_FIT
ENZYME = 2*AZOLE_FIT

# Initial condition 
## States [R1,E1,C1,R2,E2,C2,R3,E3,C3,P,R1a,C1a,C2a,R2a,R3a,R4a,C3a,Pa]
Y0_s2 = [LANOSTEROL,ENZYME,0,0,ENZYME,0,0,ENZYME,0,0,AZOLE_FIT,0,0,0,0,0,0,0]

## Parameters [kf1,kb1,kf4,kf2,kb2,kf5,kf3,kb3,kf6,kf1a,kb1a,kf2a,kb2a,kf4a,kf3a,kb3a,kf7a,kf5a,kf6a]
K0_azole = [0.0001,0.1,0.2,0.000045,0.1,0.09,0.1,0.1,0.001113,0.1,0.0056,0.000078,0.1,0.1,0.4,0.1,0.02134,0.00181,0.0013]

y_s2 = []

# Time span (in minutes)
t = np.linspace(0, DAYS*24*60, DAYS*STEPS)

y_s2 = odeint(model, Y0_s2, t, (K0_azole,))

# Sterol Composition (Kelly, 1997)
# R1 - Lanosterol: 0.73%
# R2 - Zymosterol: 0.73%
# R3 - Episterol: 0.73%
# P - Ergosterol: 2%
# R2a - Eburicol: 16.1%
# R3a - Obtusifoliol: 34.5%
# R4a - 14a-methylfecosterol: 0%
# Pa - 14a-methyl-3,6-diol: 45.2%
sterol_total = y_s2[-1,0] + y_s2[-1,3] + y_s2[-1,6] + y_s2[-1,9] + y_s2[-1,13] + y_s2[-1,14] + y_s2[-1,15] + y_s2[-1,17]
print('Lanosterol: {val:.2f} ({pct:.2f}%)'.format(val=y_s2[-1,0], pct=(y_s2[-1,0]/sterol_total)*100))
print('Zymosterol: {val:.2f} ({pct:.2f}%)'.format(val=y_s2[-1,3], pct=(y_s2[-1,3]/sterol_total)*100))
print('Episterol: {val:.2f} ({pct:.2f}%)'.format(val=y_s2[-1,6], pct=(y_s2[-1,6]/sterol_total)*100))
print('Ergosterol: {val:.2f} ({pct:.2f}%)'.format(val=y_s2[-1,9], pct=(y_s2[-1,9]/sterol_total)*100))
print('')
print('Eburicol: {val:.2f} ({pct:.2f}%)'.format(val=y_s2[-1,13], pct=(y_s2[-1,13]/sterol_total)*100))
print('Obtusifoliol: {val:.2f} ({pct:.2f}%)'.format(val=y_s2[-1,14], pct=(y_s2[-1,14]/sterol_total)*100))
print('14a-methylfecosterol: {val:.2f} ({pct:.2f}%)'.format(val=y_s2[-1,15], pct=(y_s2[-1,15]/sterol_total)*100))
print('14a-methyl-3,6-diol: {val:.2f} ({pct:.2f}%)'.format(val=y_s2[-1,17], pct=(y_s2[-1,17]/sterol_total)*100))
print('')
print('% Ergosterol reduction: {pct:.2f}%'.format(pct=((y_s1[-1,9]-y_s2[-1,9])/y_s1[-1,9])*100))

Lanosterol: 8.78 (0.70%)
Zymosterol: 8.07 (0.64%)
Episterol: 6.23 (0.50%)
Ergosterol: 25.14 (2.00%)

Eburicol: 202.31 (16.12%)
Obtusifoliol: 435.05 (34.66%)
14a-methylfecosterol: 2.19 (0.17%)
14a-methyl-3,6-diol: 567.29 (45.20%)

% Ergosterol reduction: 97.96%


### Plots generated by the model calibrated from Kelly et al., (1997) (Figure S1)

In [ ]:
# Plot
fig, axs = plt.subplots(5, 4, sharex=True, sharey=False, figsize=(38,38), dpi=300)
BLUE = 'tab:blue'
RED = 'tab:red'

axs[0,0].plot(t/60, y_s1[:,0], color=BLUE, label='(-) Azole')
axs[0,0].plot(t/60, y_s2[:,0], color=RED, label='(+) Azole', linestyle='--')
axs[0,0].set_ylabel('Lanosterol [uM]')
axs[0,0].legend()

axs[0,1].plot(t/60, y_s1[:,1], color=BLUE)
axs[0,1].plot(t/60, y_s2[:,1], color=RED, linestyle='--')
axs[0,1].set_ylabel('C14a-demethylase [uM]')

axs[0,2].plot(t/60, y_s1[:,2], color=BLUE)
axs[0,2].plot(t/60, y_s2[:,2], color=RED, linestyle='--')
axs[0,2].set_ylabel('Lanosterol-\nC14a-demethylase [uM]')

axs[0,3].plot(t/60, y_s1[:,3], color=BLUE)
axs[0,3].plot(t/60, y_s2[:,3], color=RED, linestyle='--')
axs[0,3].set_ylabel('Zymosterol [uM]')

axs[1,0].plot(t/60, y_s1[:,4], color=BLUE)
axs[1,0].plot(t/60, y_s2[:,4], color=RED, linestyle='--')
axs[1,0].set_ylabel('Sterol-methyltransferase [uM]')

axs[1,1].plot(t/60, y_s1[:,5], color=BLUE)
axs[1,1].plot(t/60, y_s2[:,5], color=RED, linestyle='--')
axs[1,1].set_ylabel('Zymosterol-\nSterol-methyltransferase [uM]')

axs[1,2].plot(t/60, y_s1[:,6], color=BLUE)
axs[1,2].plot(t/60, y_s2[:,6], color=RED, linestyle='--')
axs[1,2].set_ylabel('Episterol [uM]')

axs[1,3].plot(t/60, y_s1[:,7], color=BLUE)
axs[1,3].plot(t/60, y_s2[:,7], color=RED, linestyle='--')
axs[1,3].set_ylabel('C5-desaturase [uM]')

axs[2,0].plot(t/60, y_s1[:,8], color=BLUE)
axs[2,0].plot(t/60, y_s2[:,8], color=RED, linestyle='--')
axs[2,0].set_ylabel('Episterol-C5-desaturase [uM]')

axs[2,1].plot(t/60, y_s1[:,9], color=BLUE)
axs[2,1].plot(t/60, y_s2[:,9], color=RED, linestyle='--')
axs[2,1].set_ylabel('Ergosterol [uM]')

axs[2,2].plot(t/60, y_s1[:,10], color=BLUE)
axs[2,2].plot(t/60, y_s2[:,10], color=RED, linestyle='--')
axs[2,2].set_ylabel('Azole [uM]')

axs[2,3].plot(t/60, y_s1[:,11], color=BLUE)
axs[2,3].plot(t/60, y_s2[:,11], color=RED, linestyle='--')
axs[2,3].set_ylabel('Azole-C14a-demethylase [uM]')

axs[3,0].plot(t/60, y_s1[:,12], color=BLUE)
axs[3,0].plot(t/60, y_s2[:,12], color=RED, linestyle='--')
axs[3,0].set_ylabel('Lanosterol-\nSterol-methyltransferase [uM]')

axs[3,1].plot(t/60, y_s1[:,13], color=BLUE)
axs[3,1].plot(t/60, y_s2[:,13], color=RED, linestyle='--')
axs[3,1].set_ylabel('Eburicol [uM]')

axs[3,2].plot(t/60, y_s1[:,14], color=BLUE)
axs[3,2].plot(t/60, y_s2[:,14], color=RED, linestyle='--')
axs[3,2].set_ylabel('Obtusifoliol [uM]')

axs[3,3].plot(t/60, y_s1[:,15], color=BLUE)
axs[3,3].plot(t/60, y_s2[:,15], color=RED, linestyle='--')
axs[3,3].set_ylabel('14a-methylfecosterol [uM]')

axs[4,0].plot(t/60, y_s1[:,16], color=BLUE)
axs[4,0].plot(t/60, y_s2[:,16], color=RED, linestyle='--')
axs[4,0].set_xlabel('Time [h]')
axs[4,0].set_ylabel('14a-methylfecosterol-\nC5-desaturase [uM]')

axs[4,1].plot(t/60, y_s1[:,17], color=BLUE)
axs[4,1].plot(t/60, y_s2[:,17], color=RED, linestyle='--')
axs[4,1].set_xlabel('Time [h]')
axs[4,1].set_ylabel('14a-methyl-3,6-diol [uM]')

axs[4,2].plot(t/60, y_s1[:,9], color=BLUE)
axs[4,2].plot(t/60, y_s2[:,9], color=RED, linestyle='--')
axs[4,2].set_xlabel('Time [h]')
axs[4,2].set_ylabel('Ergosterol [uM]')
axs[4,2].spines['bottom'].set_lw(4)
axs[4,2].spines['top'].set_lw(4)
axs[4,2].spines['right'].set_lw(4)
axs[4,2].spines['left'].set_lw(4)

axs[4,3].plot(t/60, y_s1[:,17], color=BLUE)
axs[4,3].plot(t/60, y_s2[:,17], color=RED, linestyle='--')
axs[4,3].set_xlabel('Time [h]')
axs[4,3].set_ylabel('Toxic sterol [uM]')
axs[4,3].spines['bottom'].set_lw(4)
axs[4,3].spines['top'].set_lw(4)
axs[4,3].spines['right'].set_lw(4)
axs[4,3].spines['left'].set_lw(4)

fig.show()
fig.savefig('figS1.pdf',format='pdf',bbox_inches='tight')

## Study 3: Model re-calibration to the MIC breakpoint for fluconazole susceptibility (Table 2)

In [ ]:
# R1 - Lanosterol
# E1 - C14a-demethylase
# C1 - Lanosterol-C14a-demethylase Complex
# R2 - Zymosterol
# E2 - Sterol-methyltransferase
# C2 - Zymosterol-Sterol-methyltransferase Complex
# R3 - Episterol
# E3 - C5-desaturase
# C3 - Episterol-C5-desaturase Complex
# P - Ergosterol
# R1a - Azole
# C1a - Azole-C14a-demethylase Complex
# C2a - Lanosterol-Sterol-methyltransferase Complex
# R2a - Eburicol
# R3a - Obtusifoliol
# R4a - 14a-methylfecosterol
# C3a - 14a-methylfecosterol-C5-desaturase Complex
# Pa - 14a-methyl-3,6-diol

STEPS = 10000
DAYS = 1                    # (Kelly, 1997)

AZOLE_FIT = 52.24*DAYS      # 16 ug/ml (Kelly, 1997)
LANOSTEROL = 25*AZOLE_FIT
ENZYME = 2*AZOLE_FIT
AZOLE = 6.53                # MIC breakpoint for susceptible: 2 ug/ml

# Initial condition 
## States [R1,E1,C1,R2,E2,C2,R3,E3,C3,P,R1a,C1a,C2a,R2a,R3a,R4a,C3a,Pa]
Y0_s3 = [LANOSTEROL,ENZYME,0,0,ENZYME,0,0,ENZYME,0,0,AZOLE,0,0,0,0,0,0,0]

y_s3 = []

# Time span (in minutes)
t = np.linspace(0, DAYS*24*60, DAYS*STEPS)

y_s3 = odeint(model, Y0_s3, t, (K0_azole,))

sterol_total = y_s3[-1,0] + y_s3[-1,3] + y_s3[-1,6] + y_s3[-1,9] + y_s3[-1,13] + y_s3[-1,14] + y_s3[-1,15] + y_s3[-1,17]
print('Lanosterol: {val:.2f} ({pct:.2f}%)'.format(val=y_s3[-1,0], pct=(y_s3[-1,0]/sterol_total)*100))
print('Zymosterol: {val:.2f} ({pct:.2f}%)'.format(val=y_s3[-1,3], pct=(y_s3[-1,3]/sterol_total)*100))
print('Episterol: {val:.2f} ({pct:.2f}%)'.format(val=y_s3[-1,6], pct=(y_s3[-1,6]/sterol_total)*100))
print('Ergosterol: {val:.2f} ({pct:.2f}%)'.format(val=y_s3[-1,9], pct=(y_s3[-1,9]/sterol_total)*100))
print('')
print('Eburicol: {val:.2f} ({pct:.2f}%)'.format(val=y_s3[-1,13], pct=(y_s3[-1,13]/sterol_total)*100))
print('Obtusifoliol: {val:.2f} ({pct:.2f}%)'.format(val=y_s3[-1,14], pct=(y_s3[-1,14]/sterol_total)*100))
print('14a-methylfecosterol: {val:.2f} ({pct:.2f}%)'.format(val=y_s3[-1,15], pct=(y_s3[-1,15]/sterol_total)*100))
print('14a-methyl-3,6-diol: {val:.2f} ({pct:.2f}%)'.format(val=y_s3[-1,17], pct=(y_s3[-1,17]/sterol_total)*100))
print('')
print('% Ergosterol reduction: {pct:.2f}%'.format(pct=((y_s1[-1,9]-y_s3[-1,9])/y_s1[-1,9])*100))

Lanosterol: 0.00 (0.00%)
Zymosterol: 75.28 (6.01%)
Episterol: 644.33 (51.47%)
Ergosterol: 65.41 (5.22%)

Eburicol: 47.81 (3.82%)
Obtusifoliol: 152.37 (12.17%)
14a-methylfecosterol: 44.75 (3.57%)
14a-methyl-3,6-diol: 222.01 (17.73%)

% Ergosterol reduction: 94.69%


### Plots generated by the model re-calibrated to the MIC breakpoint for fluconazole susceptibility (Figure 3)

In [ ]:
# Plot
fig, axs = plt.subplots(5, 4, sharex=True, sharey=False, figsize=(38,38), dpi=300)
BLUE = 'tab:blue'
RED = 'tab:red'

axs[0,0].plot(t/60, y_s1[:,0], color=BLUE, label='(-) Azole')
axs[0,0].plot(t/60, y_s3[:,0], color=RED, label='(+) Azole', linestyle='--')
axs[0,0].set_ylabel('Lanosterol [uM]')
axs[0,0].legend()

axs[0,1].plot(t/60, y_s1[:,1], color=BLUE)
axs[0,1].plot(t/60, y_s3[:,1], color=RED, linestyle='--')
axs[0,1].set_ylabel('C14a-demethylase [uM]')

axs[0,2].plot(t/60, y_s1[:,2], color=BLUE)
axs[0,2].plot(t/60, y_s3[:,2], color=RED, linestyle='--')
axs[0,2].set_ylabel('Lanosterol-\nC14a-demethylase [uM]')

axs[0,3].plot(t/60, y_s1[:,3], color=BLUE)
axs[0,3].plot(t/60, y_s3[:,3], color=RED, linestyle='--')
axs[0,3].set_ylabel('Zymosterol [uM]')

axs[1,0].plot(t/60, y_s1[:,4], color=BLUE)
axs[1,0].plot(t/60, y_s3[:,4], color=RED, linestyle='--')
axs[1,0].set_ylabel('Sterol-methyltransferase [uM]')

axs[1,1].plot(t/60, y_s1[:,5], color=BLUE)
axs[1,1].plot(t/60, y_s3[:,5], color=RED, linestyle='--')
axs[1,1].set_ylabel('Zymosterol-\nSterol-methyltransferase [uM]')

axs[1,2].plot(t/60, y_s1[:,6], color=BLUE)
axs[1,2].plot(t/60, y_s3[:,6], color=RED, linestyle='--')
axs[1,2].set_ylabel('Episterol [uM]')

axs[1,3].plot(t/60, y_s1[:,7], color=BLUE)
axs[1,3].plot(t/60, y_s3[:,7], color=RED, linestyle='--')
axs[1,3].set_ylabel('C5-desaturase [uM]')

axs[2,0].plot(t/60, y_s1[:,8], color=BLUE)
axs[2,0].plot(t/60, y_s3[:,8], color=RED, linestyle='--')
axs[2,0].set_ylabel('Episterol-C5-desaturase [uM]')

axs[2,1].plot(t/60, y_s1[:,9], color=BLUE)
axs[2,1].plot(t/60, y_s3[:,9], color=RED, linestyle='--')
axs[2,1].set_ylabel('Ergosterol [uM]')

axs[2,2].plot(t/60, y_s1[:,10], color=BLUE)
axs[2,2].plot(t/60, y_s3[:,10], color=RED, linestyle='--')
axs[2,2].set_ylabel('Azole [uM]')

axs[2,3].plot(t/60, y_s1[:,11], color=BLUE)
axs[2,3].plot(t/60, y_s3[:,11], color=RED, linestyle='--')
axs[2,3].set_ylabel('Azole-C14a-demethylase [uM]')

axs[3,0].plot(t/60, y_s1[:,12], color=BLUE)
axs[3,0].plot(t/60, y_s3[:,12], color=RED, linestyle='--')
axs[3,0].set_ylabel('Lanosterol-\nSterol-methyltransferase [uM]')

axs[3,1].plot(t/60, y_s1[:,13], color=BLUE)
axs[3,1].plot(t/60, y_s3[:,13], color=RED, linestyle='--')
axs[3,1].set_ylabel('Eburicol [uM]')

axs[3,2].plot(t/60, y_s1[:,14], color=BLUE)
axs[3,2].plot(t/60, y_s3[:,14], color=RED, linestyle='--')
axs[3,2].set_ylabel('Obtusifoliol [uM]')

axs[3,3].plot(t/60, y_s1[:,15], color=BLUE)
axs[3,3].plot(t/60, y_s3[:,15], color=RED, linestyle='--')
axs[3,3].set_ylabel('14a-methylfecosterol [uM]')

axs[4,0].plot(t/60, y_s1[:,16], color=BLUE)
axs[4,0].plot(t/60, y_s3[:,16], color=RED, linestyle='--')
axs[4,0].set_xlabel('Time [h]')
axs[4,0].set_ylabel('14a-methylfecosterol-\nC5-desaturase [uM]')

axs[4,1].plot(t/60, y_s1[:,17], color=BLUE)
axs[4,1].plot(t/60, y_s3[:,17], color=RED, linestyle='--')
axs[4,1].set_xlabel('Time [h]')
axs[4,1].set_ylabel('14a-methyl-3,6-diol [uM]')

axs[4,2].plot(t/60, y_s1[:,9], color=BLUE)
axs[4,2].plot(t/60, y_s3[:,9], color=RED, linestyle='--')
axs[4,2].set_xlabel('Time [h]')
axs[4,2].set_ylabel('Ergosterol [uM]')
axs[4,2].spines['bottom'].set_lw(4)
axs[4,2].spines['top'].set_lw(4)
axs[4,2].spines['right'].set_lw(4)
axs[4,2].spines['left'].set_lw(4)

axs[4,3].plot(t/60, y_s1[:,17], color=BLUE)
axs[4,3].plot(t/60, y_s3[:,17], color=RED, linestyle='--')
axs[4,3].set_xlabel('Time [h]')
axs[4,3].set_ylabel('Toxic sterol [uM]')
axs[4,3].spines['bottom'].set_lw(4)
axs[4,3].spines['top'].set_lw(4)
axs[4,3].spines['right'].set_lw(4)
axs[4,3].spines['left'].set_lw(4)

fig.show()
fig.savefig('fig3.pdf',format='pdf',bbox_inches='tight')